In [1]:
import requests
import json
import pandas as pd
import sys
sys.path.insert(0,"/home/yunye/gwaslab/gwaslab/src")
import gwaslab as gl

In [2]:
# Set variables object of arguments to be passed to endpoint
# Set base URL of GraphQL API endpoint
base_url = "https://www.ebi.ac.uk/gwas/rest/api/efoTraits/MONDO_0004247/associations?projection=associationByEfoTrait"

# Perform POST request and check status code of response
r = requests.get(base_url)
print(r.status_code)

# Transform API response from JSON into Python dictionary and print in console
api_response = json.loads(r.text)
api_response

200


{'_embedded': {'associations': [{'range': None,
    'snps': [{'rsId': 'rs12532051',
      'merged': 0,
      'functionalClass': 'intron_variant',
      'lastUpdateDate': '2021-06-25T04:18:22.499+0000',
      'locations': [{'chromosomeName': '7',
        'chromosomePosition': 148109889,
        'region': {'name': '7q35'},
        '_links': {'snps': {'href': 'https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/rs12532051{?projection}',
          'templated': True}}}],
      'genomicContexts': [{'isIntergenic': False,
        'isUpstream': False,
        'isDownstream': False,
        'distance': 0,
        'gene': {'geneName': 'CNTNAP2',
         'entrezGeneIds': [{'entrezGeneId': '26047'}],
         'ensemblGeneIds': [{'ensemblGeneId': 'ENSG00000278728'},
          {'ensemblGeneId': 'ENSG00000174469'}]},
        'location': {'chromosomeName': '7',
         'chromosomePosition': 148109889,
         'region': {'name': '7q35'},
         '_links': {'snps': {'href': 'https://ww

In [37]:
for i in api_response["_embedded"]["associations"]:
    #if i is dict:
    print(i["snps"][0]["genomicContexts"][0].keys())
        

dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_links'])
dict_keys(['isIntergenic', 'isUpstream', 'isDownstream', 'distance', 'gene', 'location', 'source', 'mappingMethod', 'isClosestGene', '_l

IndexError: list index out of range

In [115]:
api_response["_embedded"]["associations"]

[{'range': '[1.31-1.49]',
  'snps': [{'rsId': 'rs75021220',
    'merged': 0,
    'functionalClass': 'intergenic_variant',
    'lastUpdateDate': '2021-06-24T20:23:26.532+0000',
    'locations': [{'chromosomeName': '4',
      'chromosomePosition': 110737238,
      'region': {'name': '4q25'},
      '_links': {'snps': {'href': 'https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/rs75021220{?projection}',
        'templated': True}}}],
    'genomicContexts': [{'isIntergenic': True,
      'isUpstream': True,
      'isDownstream': False,
      'distance': 95115,
      'gene': {'geneName': 'PITX2',
       'entrezGeneIds': [{'entrezGeneId': '5308'}],
       'ensemblGeneIds': [{'ensemblGeneId': 'ENSG00000164093'}]},
      'location': {'chromosomeName': '4',
       'chromosomePosition': 110737238,
       'region': {'name': '4q25'},
       '_links': {'snps': {'href': 'https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/rs75021220{?projection}',
         'templated': Tru

In [3]:
def gwascatalog_trait(efo):
    base_url = "https://www.ebi.ac.uk/gwas/rest/api/efoTraits/"+efo+"/associations?projection=associationByEfoTrait"
    print("Start to retrieve data from GWASCatalog...")
    print(" -Requesting GWAS associations through the following GWASCatalog API...")
    print(" -api: "+ base_url)
    # Perform POST request and check status code of response
    r = requests.get(base_url)
    if r.status_code == 200:
        print(" -Retrieved data from GWASCatalog successffully ...")
    print(" -Loading json ...")
    # Transform API response from JSON into Python dictionary and print in console
    api_response = json.loads(r.text)
    records=[]
    sig_level = 5e-8
    print(" -Parsing json ...")

    records=list()
    source="NCBI"
    print("Number of associations:",len( api_response["_embedded"]["associations"]))
    for association in api_response["_embedded"]["associations"]:
        #association statistics:
        
        p=float(association["pvalue"])    
        if p < sig_level:
            try:
                function_class=association["functionalClass"] 
            except:
                function_class=None
            try:
                eaf=association["riskFrequency"]
            except:
                eaf= None
            try:
                study=association["study"]['publicationInfo']["title"]
                pubmedid=association["study"]['publicationInfo']["pubmedId"]
            except:
                study= None
                pubmedid = None
            try:
                gene = association["loci"][0]["authorReportedGenes"][0]["geneName"]
            except:
                gene = None
            try:
                OR=association["orPerCopyNum"]
            except:
                OR=None
            try:
                beta=association["betaNum"]
                se=association["standardError"]
            except:
                beta=None
                se=None    

            for snp in association["snps"]:
                if len(snp["locations"])>0:
                    for record_num in range(len(snp["locations"])):
                        if snp["locations"][record_num]["chromosomeName"] in [str(i) for i in range(1,26)]+["x","X","y","Y","mt","MT"]:
                            if len(snp["genomicContexts"])>0:
                                closegenes=set()
                                distances=set()
                                ingene=set()
                                for gene_num in range(len(snp["genomicContexts"])):
                                    if snp["genomicContexts"][gene_num]["source"]==source:
                                        distance= str(snp["genomicContexts"][gene_num]["distance"])
                                        ingene_name = snp["genomicContexts"][gene_num]["gene"]["geneName"]
                                        if distance==0:
                                            ingene.add(ingene_name)
                                            continue
                                        if snp["genomicContexts"][gene_num]["isClosestGene"] is True:
                                            closegene_name = snp["genomicContexts"][gene_num]["gene"]["geneName"]
                                            closegenes.add(closegene_name)
                                            distances.add(distance)

                                if len(ingene)>0:
                                    autogenes =  ",".ingene
                                else:
                                    autogenes = ",".join(closegenes)

                                row=[ snp["rsId"],
                                      snp["locations"][record_num]["chromosomeName"],
                                      snp["locations"][record_num]["chromosomePosition"],
                                      gene,
                                      autogenes,
                                      function_class,
                                      OR,
                                      beta,
                                      se,
                                      p,
                                      association["study"]["diseaseTrait"]["trait"],
                                      study,
                                      pubmedid
                                    ]
                                records.append(row)
            #rsid locations
    gwascatalog = pd.DataFrame(records,columns=["SNPID","CHR","POS","REPORT_GENENAME","CLOSEST_GENENAMES","FUNCTION_CLASS","OR","BETA","SE","P","TRAIT","STUDY","PUBMEDID"])
    sigs = gl.Sumstats(gwascatalog,fmt="gwaslab",other=['REPORT_GENENAME', 'CLOSEST_GENENAMES','TRAIT', 'STUDY', 'PUBMEDID'],verbose=False)
    sigs.fix_pos(verbose=False)
    sigs.fix_chr(verbose=False)
    sigs.sort_coordinate()
    return sigs.data

In [21]:
known = gwascatalog_trait(efo="HP_0002140") 

Start to retrieve data from GWASCatalog...
 -Requesting GWAS associations through the following GWASCatalog API...
 -api: https://www.ebi.ac.uk/gwas/rest/api/efoTraits/HP_0002140/associations?projection=associationByEfoTrait
 -Retrieved data from GWASCatalog successffully ...
 -Loading json ...
 -Parsing json ...
Number of associations: 429
Thu Oct 27 00:13:50 2022 Start to sort the genome coordinates...
Thu Oct 27 00:13:50 2022  -Current Dataframe shape : 198  x  13
Thu Oct 27 00:13:50 2022  -Force converting POS to integers...
Thu Oct 27 00:13:50 2022  -Sorting genome coordinates...
Thu Oct 27 00:13:50 2022 Finished sorting genome coordinates successfully!


In [5]:
known

SNPID  CHR        POS  BETA  SE             P     OR   STATUS  \
0       rs880315    1   10736809   NaN NaN  6.000000e-09    NaN  9990999   
1       rs491203    1   15102737   NaN NaN  8.000000e-09    NaN  9990999   
2    rs138364069    1   50832533   NaN NaN  7.000000e-09  3.570  9990999   
3      rs3176471    1   50973784   NaN NaN  4.000000e-08  3.700  9990999   
4      rs1892534    1   65640261   NaN NaN  2.000000e-16    NaN  9990999   
..           ...  ...        ...   ...  ..           ...    ...      ...   
193    rs1800961   20   44413724   NaN NaN  1.000000e-10    NaN  9990999   
194    rs9808651   21   39094542   NaN NaN  6.000000e-22    NaN  9990999   
195    rs5750823   22   39433968   NaN NaN  1.000000e-12    NaN  9990999   
196   rs75347843   22   50673933   NaN NaN  6.000000e-11    NaN  9990999   
197  rs114209171   23  155050522   NaN NaN  7.000000e-13  1.153  9990999   

    REPORT_GENENAME       CLOSEST_GENENAMES  \
0             CASZ1      PEX14,LOC105376733   
1            TMEM51              TMEM51-AS1   
2              FAF1          MRPS6P2,PHBP12   
3            CDKN2C            FAF1,MIR4421   
4              None  RN7SL854P,LOC100422694   
..              ...                     ...   
193            None       MIR3646,LINC01430   
194            None  RPL23AP12,LOC107985484   
195            None            SYNGR1,MGAT3   
196            None          ARSA,RNU6-409P   
197              F8                 F8,CMC4   

                                                 TRAIT  \
0                                      Ischemic stroke   
1    Acute ischemic stroke x type 2 diabetes intera...   
2       Ischemic stroke (large artery atherosclerosis)   
3       Ischemic stroke (large artery atherosclerosis)   
4    Ischemic stroke or fibrinogen levels (pleiotropy)   
..                                                 ...   
193  Ischemic stroke or fibrinogen levels (pleiotropy)   
194  Ischemic stroke or fibrinogen levels (pleiotropy)   
195  Ischemic stroke or von Willebrand factor level...   
196  Ischemic stroke or fibrinogen levels (pleiotropy)   
197                                         Thrombosis   

                                                 STUDY  PUBMEDID  
0    Multiancestry genome-wide association study of...  29531354  
1    Discovery of 318 new risk loci for type 2 diab...  32541925  
2    Genome-Wide Association Analysis of Young-Onse...  26732560  
3    Genome-Wide Association Analysis of Young-Onse...  26732560  
4    Multi-phenotype analyses of hemostatic traits ...  35285134  
..                                                 ...       ...  
193  Multi-phenotype analyses of hemostatic traits ...  35285134  
194  Multi-phenotype analyses of hemostatic traits ...  35285134  
195  Multi-phenotype analyses of hemostatic traits ...  35285134  
196  Multi-phenotype analyses of hemostatic traits ...  35285134  
197  Genome-wide association analysis of self-repor...  26908601  

[198 rows x 13 columns]

In [155]:
!wget -O t2d_bbj.txt.gz http://jenger.riken.jp/14/

--2022-10-26 23:54:33--  http://jenger.riken.jp/14/
Resolving jenger.riken.jp (jenger.riken.jp)... 134.160.84.25
Connecting to jenger.riken.jp (jenger.riken.jp)|134.160.84.25|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 274187574 (261M) [text/plain]
Saving to: ‘t2d_bbj.txt.gz’

t2d_bbj.txt.gz      100%[===================>] 261.49M  11.1MB/s    in 24s     

2022-10-26 23:55:24 (10.8 MB/s) - ‘t2d_bbj.txt.gz’ saved [274187574/274187574]



Thu Oct 27 00:58:00 2022 Start to initiate from file :t2d_bbj.txt.gz
Thu Oct 27 00:58:01 2022  -Reading columns          : POS,BETA,N,REF,P,ALT,SE,Frq,Dir,SNP,CHR
Thu Oct 27 00:58:01 2022  -Renaming columns to      : POS,BETA,N,NEA,P,EA,SE,EAF,DIRECTION,SNPID,CHR
Thu Oct 27 00:58:01 2022  -Current dataframe shape  : Rows  1000000  x  11  Columns
Thu Oct 27 00:58:01 2022  -Initiating a status column ...
Thu Oct 27 00:58:01 2022  -Reordering columns to    : SNPID,CHR,POS,EA,NEA,EAF,BETA,SE,P,N,DIRECTION,STATUS
Thu Oct 27 00:58:01 2022  -NEAF is specified...
Thu Oct 27 00:58:01 2022  -Checking if 0<= NEAF <=1 ...
Thu Oct 27 00:58:01 2022  -Converted NEAF to EAF.
Thu Oct 27 00:58:01 2022  -Removed 0 variants with bad NEAF.
Thu Oct 27 00:58:01 2022 Finished loading data successfully!


Thu Oct 27 00:58:01 2022 Start to check IDs...
Thu Oct 27 00:58:01 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 00:58:01 2022  -Checking if SNPID is chr:pos:ref:alt...(separator: - ,: , _)
Thu Oct 27 00:58:03 2022 Finished checking IDs successfully!
Thu Oct 27 00:58:03 2022 Start to fix chromosome notation...
Thu Oct 27 00:58:03 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 00:58:05 2022  -All CHR are already fixed...
Thu Oct 27 00:58:06 2022 Finished fixing chromosome notation successfully!
Thu Oct 27 00:58:06 2022 Start to fix basepair positions...
Thu Oct 27 00:58:06 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 00:58:07 2022  -Position upper_bound is: 250,000,000
Thu Oct 27 00:58:09 2022  -Remove outliers: 0
Thu Oct 27 00:58:09 2022  -Converted all position to datatype Int64.
Thu Oct 27 00:58:09 2022 Finished fixing basepair position successfully!
Thu Oct 27 00:58:09 2022 Start to fix alleles...
Thu Oct 27 00:58:09 2022  -Current Dataframe sh

In [6]:
mysumstats.liftover(from_build="19",to_build="38",n_cores=4)

Thu Oct 27 00:58:12 2022 Start to perform liftover...
Thu Oct 27 00:58:12 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 00:58:12 2022  -CPU Cores to use : 4
Thu Oct 27 00:58:12 2022  -Performing liftover ...
Thu Oct 27 00:58:12 2022  -Creating converter : hg19 to hg38
Thu Oct 27 00:58:12 2022  -Converting variants with status code xxx0xxx :1000000...
Thu Oct 27 00:59:23 2022  -Removed unmapped variants: 619
Thu Oct 27 00:59:28 2022 Finished liftover successfully!


In [7]:
mysumstats.data

SNPID  CHR      POS   EA NEA     EAF    BETA      SE  \
0         1:725932_G_A    1   790552    G   A  0.9960 -0.0737  0.1394   
1         1:725933_A_G    1   790553    G   A  0.0040  0.0737  0.1394   
2         1:737801_T_C    1   802421    C   T  0.0051  0.0490  0.1231   
3       1:749963_T_TAA    1   814583  TAA   T  0.8374  0.0213  0.0199   
4         1:751343_T_A    1   815963    T   A  0.8593  0.0172  0.0156   
...                ...  ...      ...  ...  ..     ...     ...     ...   
999995   2:6347639_C_A    2  6207507    C   A  0.7900 -0.0159  0.0111   
999996   2:6347694_G_C    2  6207562    G   C  0.7907 -0.0151  0.0111   
999997   2:6348478_G_A    2  6208346    G   A  0.7860 -0.0152  0.0111   
999998   2:6348490_G_C    2  6208358    G   C  0.9985 -0.3180  0.2032   
999999   2:6348754_A_C    2  6208622    C   A  0.1572  0.0297  0.0126   

              P       N DIRECTION   STATUS  
0       0.59700  166718      -?+-  3860099  
1       0.59730  166718      +?-+  3860099  
2       0.69080  166718      +?-+  3860099  
3       0.28460  166718      -?++  3860399  
4       0.27050  166718      -?++  3860099  
...         ...     ...       ...      ...  
999995  0.15100  191764      ---+  3860099  
999996  0.17250  191764      ---+  3860099  
999997  0.17160  191764      ---+  3860099  
999998  0.11750  191764      +---  3860099  
999999  0.01846  191764      +++-  3860099  

[999381 rows x 12 columns]

In [23]:
known = gwascatalog_trait(efo="MONDO_0005148") 

Start to retrieve data from GWASCatalog...
 -Requesting GWAS associations through the following GWASCatalog API...
 -api: https://www.ebi.ac.uk/gwas/rest/api/efoTraits/MONDO_0005148/associations?projection=associationByEfoTrait
 -Retrieved data from GWASCatalog successffully ...
 -Loading json ...
 -Parsing json ...
Number of associations: 5253
Thu Oct 27 00:35:03 2022 Start to sort the genome coordinates...
Thu Oct 27 00:35:03 2022  -Current Dataframe shape : 3939  x  13
Thu Oct 27 00:35:03 2022  -Force converting POS to integers...
Thu Oct 27 00:35:03 2022  -Sorting genome coordinates...
Thu Oct 27 00:35:03 2022 Finished sorting genome coordinates successfully!


In [24]:
known

SNPID  CHR        POS    BETA      SE              P        OR  \
0     rs12741141    1    6609910  0.0395  0.0048   1.000000e-16       NaN   
1     rs11583755    1    6612669  0.0369  0.0041   1.000000e-19       NaN   
2      rs1010447    1   11209739     NaN     NaN   2.000000e-08       NaN   
3      rs4845987    1   11246222  0.0282  0.0051   3.000000e-08       NaN   
4      rs7554251    1   11257875  0.0297  0.0045   3.000000e-11       NaN   
...          ...  ...        ...     ...     ...            ...       ...   
3934   rs5945326   23  153634467     NaN     NaN   2.000000e-12  1.140000   
3935   rs5945326   23  153634467     NaN     NaN   3.000000e-10  1.270000   
3936   rs5945326   23  153634467  0.1203  0.0055  8.000000e-106       NaN   
3937   rs1894299   23  153643433     NaN     NaN   9.000000e-58  1.130000   
3938   rs1894299   23  153643433     NaN     NaN   2.000000e-67  0.884338   

       STATUS REPORT_GENENAME       CLOSEST_GENENAMES  \
0     9990999              NR            KLHL21,PHF13   
1     9990999              NR            KLHL21,PHF13   
2     9990999            MTOR       RNU6-291P,ANGPTL7   
3     9990999              NR          RPL39P6,UBIAD1   
4     9990999              NR          RPL39P6,UBIAD1   
...       ...             ...                     ...   
3934  9990999           DUSP9      LOC105373384,DUSP9   
3935  9990999           DUSP9      LOC105373384,DUSP9   
3936  9990999            None      LOC105373384,DUSP9   
3937  9990999           DUSP9  LOC105373384,RPL18AP16   
3938  9990999            None  LOC105373384,RPL18AP16   

                                               TRAIT  \
0                                    Type 2 diabetes   
1                                    Type 2 diabetes   
2     Body mass index and type 2 diabetes (pairwise)   
3                                    Type 2 diabetes   
4                                    Type 2 diabetes   
...                                              ...   
3934                                 Type 2 diabetes   
3935                                 Type 2 diabetes   
3936                                 Type 2 diabetes   
3937                                 Type 2 diabetes   
3938                                 Type 2 diabetes   

                                                  STUDY  PUBMEDID  
0     Discovery of 318 new risk loci for type 2 diab...  32541925  
1     Discovery of 318 new risk loci for type 2 diab...  32541925  
2     Genome-wide discovery of genetic loci that unc...  33619380  
3     Discovery of 318 new risk loci for type 2 diab...  32541925  
4     Discovery of 318 new risk loci for type 2 diab...  32541925  
...                                                 ...       ...  
3934  Genome-wide association study identifies three...  23945395  
3935  Twelve type 2 diabetes susceptibility loci ide...  20581827  
3936  A cross-population atlas of genetic associatio...  34594039  
3937  Identification of 28 new susceptibility loci f...  30718926  
3938  Large-scale genome-wide association study in a...  32514122  

[3939 rows x 13 columns]

In [27]:
known.to_csv("t2d_known.txt",index=None)

In [1]:
import requests
import json
import pandas as pd
import sys
sys.path.insert(0,"/home/yunye/gwaslab/gwaslab/src")
import gwaslab as gl

In [2]:
mysumstats = gl.Sumstats("t2d_bbj.txt.gz",
             snpid="SNP",
             chrom="CHR",
             pos="POS",
             ea="ALT",
             nea="REF",
             neaf="Frq",
             beta="BETA",
             se="SE",
             p="P",
             direction="Dir",
             n="N",nrows=1000000)

Thu Oct 27 01:33:16 2022 Start to initiate from file :t2d_bbj.txt.gz
Thu Oct 27 01:33:17 2022  -Reading columns          : CHR,REF,P,POS,SE,BETA,ALT,SNP,Dir,Frq,N
Thu Oct 27 01:33:17 2022  -Renaming columns to      : CHR,NEA,P,POS,SE,BETA,EA,SNPID,DIRECTION,EAF,N
Thu Oct 27 01:33:17 2022  -Current dataframe shape  : Rows  1000000  x  11  Columns
Thu Oct 27 01:33:17 2022  -Initiating a status column ...
Thu Oct 27 01:33:17 2022  -Reordering columns to    : SNPID,CHR,POS,EA,NEA,EAF,BETA,SE,P,N,DIRECTION,STATUS
Thu Oct 27 01:33:18 2022  -NEAF is specified...
Thu Oct 27 01:33:18 2022  -Checking if 0<= NEAF <=1 ...
Thu Oct 27 01:33:18 2022  -Converted NEAF to EAF.
Thu Oct 27 01:33:18 2022  -Removed 0 variants with bad NEAF.
Thu Oct 27 01:33:18 2022 Finished loading data successfully!


In [3]:
mysumstats.basic_check()

Thu Oct 27 01:33:18 2022 Start to check IDs...
Thu Oct 27 01:33:18 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 01:33:18 2022  -Checking if SNPID is chr:pos:ref:alt...(separator: - ,: , _)
Thu Oct 27 01:33:19 2022 Finished checking IDs successfully!
Thu Oct 27 01:33:19 2022 Start to fix chromosome notation...
Thu Oct 27 01:33:19 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 01:33:21 2022  -All CHR are already fixed...
Thu Oct 27 01:33:23 2022 Finished fixing chromosome notation successfully!
Thu Oct 27 01:33:23 2022 Start to fix basepair positions...
Thu Oct 27 01:33:23 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 01:33:24 2022  -Position upper_bound is: 250,000,000
Thu Oct 27 01:33:25 2022  -Remove outliers: 0
Thu Oct 27 01:33:26 2022  -Converted all position to datatype Int64.
Thu Oct 27 01:33:26 2022 Finished fixing basepair position successfully!
Thu Oct 27 01:33:26 2022 Start to fix alleles...
Thu Oct 27 01:33:26 2022  -Current Dataframe sh

In [7]:
mysumstats.liftover(from_build="19",to_build="38",n_cores=4)

Thu Oct 27 01:34:28 2022 Start to perform liftover...
Thu Oct 27 01:34:28 2022  -Current Dataframe shape : 1000000  x  12
Thu Oct 27 01:34:28 2022  -CPU Cores to use : 4
Thu Oct 27 01:34:28 2022  -Performing liftover ...
Thu Oct 27 01:34:28 2022  -Creating converter : hg19 to hg38
Thu Oct 27 01:34:29 2022  -Converting variants with status code xxx0xxx :1000000...
Thu Oct 27 01:35:39 2022  -Removed unmapped variants: 619
Thu Oct 27 01:35:45 2022 Finished liftover successfully!


In [4]:
known = pd.read_csv("t2d_known.txt")

In [5]:
known

SNPID  CHR        POS    BETA      SE              P        OR  \
0     rs12741141    1    6609910  0.0395  0.0048   1.000000e-16       NaN   
1     rs11583755    1    6612669  0.0369  0.0041   1.000000e-19       NaN   
2      rs1010447    1   11209739     NaN     NaN   2.000000e-08       NaN   
3      rs4845987    1   11246222  0.0282  0.0051   3.000000e-08       NaN   
4      rs7554251    1   11257875  0.0297  0.0045   3.000000e-11       NaN   
...          ...  ...        ...     ...     ...            ...       ...   
3934   rs5945326   23  153634467     NaN     NaN   2.000000e-12  1.140000   
3935   rs5945326   23  153634467     NaN     NaN   3.000000e-10  1.270000   
3936   rs5945326   23  153634467  0.1203  0.0055  8.000000e-106       NaN   
3937   rs1894299   23  153643433     NaN     NaN   9.000000e-58  1.130000   
3938   rs1894299   23  153643433     NaN     NaN   2.000000e-67  0.884338   

       STATUS REPORT_GENENAME       CLOSEST_GENENAMES  \
0     9990999              NR            KLHL21,PHF13   
1     9990999              NR            KLHL21,PHF13   
2     9990999            MTOR       RNU6-291P,ANGPTL7   
3     9990999              NR          RPL39P6,UBIAD1   
4     9990999              NR          RPL39P6,UBIAD1   
...       ...             ...                     ...   
3934  9990999           DUSP9      LOC105373384,DUSP9   
3935  9990999           DUSP9      LOC105373384,DUSP9   
3936  9990999             NaN      LOC105373384,DUSP9   
3937  9990999           DUSP9  LOC105373384,RPL18AP16   
3938  9990999             NaN  LOC105373384,RPL18AP16   

                                               TRAIT  \
0                                    Type 2 diabetes   
1                                    Type 2 diabetes   
2     Body mass index and type 2 diabetes (pairwise)   
3                                    Type 2 diabetes   
4                                    Type 2 diabetes   
...                                              ...   
3934                                 Type 2 diabetes   
3935                                 Type 2 diabetes   
3936                                 Type 2 diabetes   
3937                                 Type 2 diabetes   
3938                                 Type 2 diabetes   

                                                  STUDY  PUBMEDID  
0     Discovery of 318 new risk loci for type 2 diab...  32541925  
1     Discovery of 318 new risk loci for type 2 diab...  32541925  
2     Genome-wide discovery of genetic loci that unc...  33619380  
3     Discovery of 318 new risk loci for type 2 diab...  32541925  
4     Discovery of 318 new risk loci for type 2 diab...  32541925  
...                                                 ...       ...  
3934  Genome-wide association study identifies three...  23945395  
3935  Twelve type 2 diabetes susceptibility loci ide...  20581827  
3936  A cross-population atlas of genetic associatio...  34594039  
3937  Identification of 28 new susceptibility loci f...  30718926  
3938  Large-scale genome-wide association study in a...  32514122  

[3939 rows x 13 columns]

In [9]:
mysumstats.get_novel(known = known,only_novel=False)

Thu Oct 27 01:35:53 2022 Start to extract lead variants...
Thu Oct 27 01:35:53 2022  -Processing 999381 variants...
Thu Oct 27 01:35:53 2022  -Significance threshold : 5e-08
Thu Oct 27 01:35:53 2022  -Sliding window size: 500  kb
Thu Oct 27 01:35:54 2022  -Found 543 significant variants in total...
Thu Oct 27 01:35:54 2022  -Identified 4 lead variants!
Thu Oct 27 01:35:54 2022 Finished extracting lead variants successfully!
Thu Oct 27 01:35:54 2022 Start to check if lead variants are known...
Thu Oct 27 01:35:54 2022  -Lead variants in known loci: 3939
Thu Oct 27 01:35:54 2022  -Checking the minimum distance between identified lead variants and provided known variants...
Thu Oct 27 01:35:54 2022  -Identified  4  known vairants in current sumstats...
Thu Oct 27 01:35:54 2022  -Identified  0  novel vairants in current sumstats...
Thu Oct 27 01:35:54 2022 Finished checking known or novel successfully!


SNPID  CHR        POS  EA    NEA     EAF    BETA      SE  \
96739     1:22068326_A_G    1   21741833   G      A  0.7550  0.0621  0.0103   
213860    1:51103268_T_C    1   50637596   C      T  0.7953 -0.0802  0.0120   
534095  1:154309595_TA_T    1  154337119  TA      T  0.0947 -0.0915  0.0166   
969974  2:640986_CACAT_C    2     640986   C  CACAT  0.9006 -0.0946  0.0150   

                   P       N DIRECTION   STATUS    TCHR+POS  \
96739   1.629000e-09  191764      ++++  3860099  1021741833   
213860  2.519000e-11  191764      ----  3860099  1050637596   
534095  3.289000e-08  191764      ----  3860399  1154337119   
969974  2.665000e-10  191764      ----  3860399  2000640986   

        DISTANCE_TO_KNOWN    KNOWN_ID  NOVEL  
96739                   0   rs1825307  False  
213860                  0  rs12031188  False  
534095                  1  rs68062313  False  
969974                  1  rs72156956  False

In [148]:
gwascatalog = pd.DataFrame(records,columns=["SNPID","CHR","POS","REPORT_GENENAME","CLOSEST_GENENAMES","FUNCTION_CLASS","OR","BETA","SE","P","TRAIT","STUDY","PUBMEDID"])
sigs = gl.Sumstats(gwascatalog,fmt="gwaslab",other=['REPORT_GENENAME', 'CLOSEST_GENENAMES','TRAIT', 'STUDY', 'PUBMEDID'],verbose=False)
sigs.fix_pos(verbose=False)
sigs.fix_chr(verbose=False)

In [147]:
sigs.data

SNPID  CHR        POS    BETA     SE             P     OR   STATUS  \
0     rs75021220    4  110737238     NaN    NaN  1.000000e-25  1.400  9990999   
1      rs7193343   16   72995261     NaN    NaN  2.000000e-10  1.170  9990999   
2      rs2200733    4  110789013     NaN    NaN  3.000000e-32  1.370  9990999   
3     rs74475935   16   15961249     NaN    NaN  5.000000e-11  4.630  9990999   
4     rs10744777   12  111795214     NaN    NaN  3.000000e-09  1.170  9990999   
..           ...  ...        ...     ...    ...           ...    ...      ...   
193   rs11880613   19   10793296  0.0613  0.011  3.000000e-08    NaN  9990999   
194    rs3897976    3   41565201     NaN    NaN  3.000000e-08  2.162  9990999   
195  rs149608518    4  164551523     NaN    NaN  1.000000e-08  5.587  9990999   
196  rs189668056    2   38081685     NaN    NaN  4.000000e-08  2.027  9990999   
197  rs139293840   17   80556559     NaN    NaN  2.000000e-08  3.511  9990999   

    REPORT_GENENAME      CLOSEST_GENENAMES  \
0             PITX2                  PITX2   
1             ZFHX3                 HCCAT5   
2             PITX2           PITX2,MIR297   
3             ABCC1           LOC107984869   
4             ALDH2         MIR6761,ACAD10   
..              ...                    ...   
193            None       MIR4748,MIR199A1   
194            None                  ALCAM   
195            None              RNU6-284P   
196            None    CYP1B1,LOC105374466   
197            None  RPL32P31,LOC105371922   

                                                 TRAIT  \
0                      Ischemic stroke (cardioembolic)   
1                      Ischemic stroke (cardioembolic)   
2                      Ischemic stroke (cardioembolic)   
3               Ischemic stroke (undetermined subtype)   
4             Ischemic stroke (small artery occlusion)   
..                                                 ...   
193                                    Ischemic stroke   
194                    Ischemic stroke in dyslipidemia   
195               Ischemic stroke in diabetes mellitus   
196     Cardio-cerebrovascular disease in dyslipidemia   
197  Cardio-cerebrovascular disease in diabetes mel...   

                                                 STUDY  PUBMEDID  
0    Identification of additional risk loci for str...  27068588  
1    Loci associated with ischaemic stroke and its ...  26708676  
2    Loci associated with ischaemic stroke and its ...  26708676  
3    Loci associated with ischaemic stroke and its ...  26708676  
4    Loci associated with ischaemic stroke and its ...  26708676  
..                                                 ...       ...  
193  A cross-population atlas of genetic associatio...  34594039  
194  Identification of susceptibility loci for card...  33632238  
195  Identification of susceptibility loci for card...  33632238  
196  Identification of susceptibility loci for card...  33632238  
197  Identification of susceptibility loci for card...  33632238  

[198 rows x 13 columns]

In [129]:
locations = pd.json_normalize(api_response["_embedded"]["associations"],"snps",errors='ignore')[["locations","genomicContexts"]]




locations  \
0   [{'chromosomeName': '8', 'chromosomePosition':...   
1   [{'chromosomeName': '19', 'chromosomePosition'...   
2   [{'chromosomeName': '8', 'chromosomePosition':...   
3   [{'chromosomeName': '11', 'chromosomePosition'...   
4   [{'chromosomeName': '1', 'chromosomePosition':...   
..                                                ...   
68  [{'chromosomeName': '19', 'chromosomePosition'...   
69  [{'chromosomeName': '3', 'chromosomePosition':...   
70  [{'chromosomeName': '19', 'chromosomePosition'...   
71  [{'chromosomeName': 'CHR_HSCHR6_MHC_DBB_CTG1',...   
72  [{'chromosomeName': 'CHR_HSCHR6_MHC_MCF_CTG1',...   

                                      genomicContexts  
0   [{'isIntergenic': False, 'isUpstream': False, ...  
1   [{'isIntergenic': True, 'isUpstream': True, 'i...  
2   [{'isIntergenic': True, 'isUpstream': False, '...  
3   [{'isIntergenic': True, 'isUpstream': True, 'i...  
4   [{'isIntergenic': True, 'isUpstream': True, 'i...  
..                                                ...  
68  [{'isIntergenic': True, 'isUpstream': False, '...  
69  [{'isIntergenic': True, 'isUpstream': True, 'i...  
70  [{'isIntergenic': True, 'isUpstream': True, 'i...  
71  [{'isIntergenic': True, 'isUpstream': True, 'i...  
72  [{'isIntergenic': True, 'isUpstream': False, '...  

[73 rows x 2 columns]

In [77]:
layer1 = pd.json_normalize(api_response["_embedded"]["associations"])
layer1

range                                               snps  \
0   [1.65-2.5]  [{'rsId': 'rs12678747', 'merged': 0, 'function...   
1           NR  [{'rsId': 'rs681343', 'merged': 0, 'functional...   
2           NR  [{'rsId': 'rs2976388', 'merged': 0, 'functiona...   
3           NR  [{'rsId': 'rs10500661', 'merged': 0, 'function...   
4           NR  [{'rsId': 'rs147048677', 'merged': 0, 'functio...   
..         ...                                                ...   
68        None  [{'rsId': 'rs11083749', 'merged': 0, 'function...   
69        None  [{'rsId': 'rs709210', 'merged': 0, 'functional...   
70        None  [{'rsId': 'rs11880948', 'merged': 0, 'function...   
71        None  [{'rsId': 'rs28732222', 'merged': 0, 'function...   
72        None  [{'rsId': 'rs17206350', 'merged': 0, 'function...   

                                                 loci riskFrequency  \
0   [{'haplotypeSnpCount': None, 'description': 'S...            NR   
1   [{'haplotypeSnpCount': None, 'description': 'S...          0.49   
2   [{'haplotypeSnpCount': None, 'description': 'S...          0.58   
3   [{'haplotypeSnpCount': None, 'description': 'S...           0.8   
4   [{'haplotypeSnpCount': None, 'description': 'S...          0.94   
..                                                ...           ...   
68  [{'haplotypeSnpCount': None, 'description': 'S...            NR   
69  [{'haplotypeSnpCount': None, 'description': 'S...            NR   
70  [{'haplotypeSnpCount': None, 'description': 'S...            NR   
71  [{'haplotypeSnpCount': None, 'description': 'S...            NR   
72  [{'haplotypeSnpCount': None, 'description': 'S...            NR   

   pvalueDescription  orPerCopyNum snpType  multiSnpHaplotype  snpInteraction  \
0               None          2.03   novel              False           False   
1               None          0.92   novel              False           False   
2               None          1.09   novel              False           False   
3               None          0.90   novel              False           False   
4               None          0.86   novel              False           False   
..               ...           ...     ...                ...             ...   
68              None           NaN   novel              False           False   
69              None           NaN   novel              False           False   
70              None           NaN   novel              False           False   
71              None           NaN   novel              False           False   
72              None           NaN   novel              False           False   

    pvalueMantissa  ...                        study.publicationInfo.title  \
0                3  ...  Genome-Wide association between EYA1 and Aspir...   
1                2  ...  GWAS of peptic ulcer disease implicates Helico...   
2                2  ...  GWAS of peptic ulcer disease implicates Helico...   
3                4  ...  GWAS of peptic ulcer disease implicates Helico...   
4                9  ...  GWAS of peptic ulcer disease implicates Helico...   
..             ...  ...                                                ...   
68               3  ...  A large-scale genome-wide cross-trait analysis...   
69               4  ...  A large-scale genome-wide cross-trait analysis...   
70               6  ...  A large-scale genome-wide cross-trait analysis...   
71               1  ...  A large-scale genome-wide cross-trait analysis...   
72               1  ...  A large-scale genome-wide cross-trait analysis...   

   study.publicationInfo.author.fullname  study.publicationInfo.author.orcid  \
0                            Bourgeois S                                None   
1                                   Wu Y                 0000-0002-5977-1526   
2                                   Wu Y                 0000-0002-5977-1526   
3                                   Wu Y                 0000-0002-5977-1526   
4                

In [78]:
layer2 = pd.json_normalize(api_response["_embedded"]["associations"],"snps")
layer2

rsId  merged          functionalClass  \
0    rs12678747       0           intron_variant   
1      rs681343       0              stop_gained   
2     rs2976388       0           intron_variant   
3    rs10500661       0       intergenic_variant   
4   rs147048677       0       synonymous_variant   
..          ...     ...                      ...   
68   rs11083749       0           intron_variant   
69     rs709210       0         missense_variant   
70   rs11880948       0           intron_variant   
71   rs28732222       0  downstream_gene_variant   
72   rs17206350       0    upstream_gene_variant   

                  lastUpdateDate  \
0   2022-03-23T17:19:52.947+0000   
1   2022-08-03T16:59:51.731+0000   
2   2021-06-24T21:12:27.021+0000   
3   2021-06-25T04:18:24.804+0000   
4   2021-06-24T21:12:28.862+0000   
..                           ...   
68  2022-09-09T17:04:12.767+0000   
69  2022-09-09T17:04:14.640+0000   
70  2022-09-09T17:04:14.970+0000   
71  2022-09-09T17:04:19.712+0000   
72  2022-09-09T17:04:24.164+0000   

                                            locations  \
0   [{'chromosomeName': '8', 'chromosomePosition':...   
1   [{'chromosomeName': '19', 'chromosomePosition'...   
2   [{'chromosomeName': '8', 'chromosomePosition':...   
3   [{'chromosomeName': '11', 'chromosomePosition'...   
4   [{'chromosomeName': '1', 'chromosomePosition':...   
..                                                ...   
68  [{'chromosomeName': '19', 'chromosomePosition'...   
69  [{'chromosomeName': '3', 'chromosomePosition':...   
70  [{'chromosomeName': '19', 'chromosomePosition'...   
71  [{'chromosomeName': 'CHR_HSCHR6_MHC_DBB_CTG1',...   
72  [{'chromosomeName': 'CHR_HSCHR6_MHC_MCF_CTG1',...   

                                      genomicContexts  
0   [{'isIntergenic': False, 'isUpstream': False, ...  
1   [{'isIntergenic': True, 'isUpstream': True, 'i...  
2   [{'isIntergenic': True, 'isUpstream': False, '...  
3   [{'isIntergenic': True, 'isUpstream': True, 'i...  
4   [{'isIntergenic': True, 'isUpstream': True, 'i...  
..                                                ...  
68  [{'isIntergenic': True, 'isUpstream': False, '...  
69  [{'isIntergenic': True, 'isUpstream': True, 'i...  
70  [{'isIntergenic': True, 'isUpstream': True, 'i...  
71  [{'isIntergenic': True, 'isUpstream': True, 'i...  
72  [{'isIntergenic': True, 'isUpstream': False, '...  

[73 rows x 6 columns]

In [80]:
layer3 = pd.json_normalize(api_response["_embedded"]["associations"],["snps","locations"])
layer3

chromosomeName  chromosomePosition region.name  \
0                           8            71202541      8q13.3   
1                           8            71202541      8q13.3   
2                          19            48703205    19q13.33   
3                           8           142678838      8q24.3   
4                          11             6252514     11p15.4   
..                        ...                 ...         ...   
107                         6            32707290     6p21.32   
108   CHR_HSCHR6_MHC_DBB_CTG1            32686300        None   
109   CHR_HSCHR6_MHC_COX_CTG1            32630720        None   
110   CHR_HSCHR6_MHC_QBL_CTG1            32635972        None   
111  CHR_HSCHR6_MHC_SSTO_CTG1            32799385        None   

                                           _links.snps  \
0    [{'href': 'https://www.ebi.ac.uk/gwas/rest/api...   
1    [{'href': 'https://www.ebi.ac.uk/gwas/rest/api...   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
..                                                 ...   
107                                                NaN   
108                                                NaN   
109                                                NaN   
110                                                NaN   
111                                                NaN   

                                      _links.snps.href _links.snps.templated  
0                                                  NaN                   NaN  
1                                                  NaN                   NaN  
2    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
3    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
4    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
..                                                 ...                   ...  
107  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
108  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
109  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
110  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
111  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  

[112 rows x 6 columns]

In [82]:
layer3.drop_duplicates(subset=["chromosomeName","chromosomePosition"])

chromosomeName  chromosomePosition region.name  \
0                           8            71202541      8q13.3   
2                          19            48703205    19q13.33   
3                           8           142678838      8q24.3   
4                          11             6252514     11p15.4   
5                           1           155192003        1q22   
..                        ...                 ...         ...   
107                         6            32707290     6p21.32   
108   CHR_HSCHR6_MHC_DBB_CTG1            32686300        None   
109   CHR_HSCHR6_MHC_COX_CTG1            32630720        None   
110   CHR_HSCHR6_MHC_QBL_CTG1            32635972        None   
111  CHR_HSCHR6_MHC_SSTO_CTG1            32799385        None   

                                           _links.snps  \
0    [{'href': 'https://www.ebi.ac.uk/gwas/rest/api...   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
5                                                  NaN   
..                                                 ...   
107                                                NaN   
108                                                NaN   
109                                                NaN   
110                                                NaN   
111                                                NaN   

                                      _links.snps.href _links.snps.templated  
0                                                  NaN                   NaN  
2    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
3    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
4    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
5    https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
..                                                 ...                   ...  
107  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
108  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
109  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
110  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  
111  https://www.ebi.ac.uk/gwas/rest/api/singleNucl...                  True  

[109 rows x 6 columns]

In [41]:
for i in api_response["_embedded"]["associations"]:
    if "pvalue" in i:
        if float(i["pvalue"])<5e-8:      
            snp = pd.json_normalize(api_response["_embedded"]["associations"][0]["snps"],max_level=0)

            
            
            if "rsId" in i["snps"][0]:
                print(i["snps"][0]["rsId"], end=",")
                if "locations" in i["snps"][0]:
                    if len(i["snps"][0]["locations"])>0:
                        print(i["snps"][0]["locations"][0]["chromosomeName"],end=" ")
                    if len(i["snps"][0]["locations"])>0:
                        print(i["snps"][0]["locations"][0]["chromosomePosition"],end=" ")   
                if "genomicContexts" in i["snps"][0]:
                    if "gene" in i["snps"][0]["genomicContexts"][0]:
                        if "geneName" in i["snps"][0]["genomicContexts"][0]["gene"]:
                            print(i["snps"][0]["genomicContexts"][0]["gene"]["geneName"])
            print(i["pvalue"])
        
        
        

rs12678747,8 71202541 EYA1
3e-11
rs681343,19 48703205 FAM83E
2e-15
rs2976388,8 142678838 SLURP2
2e-14
rs10500661,11 6252514 OR52B2
4e-14
rs147048677,1 155192003 HMGN2P18
9e-12
rs78459074,CHR_HSCHR11_2_CTG1 1036727 AP2A2
3e-10
rs34074411,17 41710996 GAST
3e-10
rs687621,9 133261662 MED22
1e-09
rs9581957,13 27983752 CDX2
4e-09
rs200964,6 27899165 H4C11
3.0000000000000003e-13
rs967823,17 52239916 CA10
2e-12
chr19:18793695,

IndexError: list index out of range

In [ ]:
for item,associations in api_response["_embedded"].items():
    associations[0]["snp"][0]["rsID"]

In [48]:
import re
pattern = re.compile(r'rs[0-9]+')

In [52]:
a=pattern.search("'https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/rs17206350{?projection}'")
a[0]

rs17206350


In [55]:
for value in api_response["_embedded"].values():
    for i in value:
        a=pattern.search(i['loci'][0]["strongestRiskAlleles"][0]["_links"]["snp"]["href"])
        if a is None:
            continue
        base_url = "https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/"+a[0]
        r = requests.get(base_url)
        snp_response = json.loads(r.text)
        print(a[0],snp_response["locations"][0]["chromosomeName"],api_response["locations"][0]["chromosomePosition"])

KeyError: '_embedded'

In [40]:
base_url = "https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/rs3852865"

# Perform POST request and check status code of response
r = requests.get(base_url)
print(r.status_code)

# Transform API response from JSON into Python dictionary and print in console
api_response = json.loads(r.text)
print(api_response["locations"][0]["chromosomeName"],api_response["locations"][0]["chromosomePosition"])

200
19 51210809
